# Encontrar farmacias en mazatlan y hospitales 

In [1]:
## ---- Librerias ---- ##
# --- Librerías únicas y ordenadas ---
import sys
import numpy as np
import pandas as pd
from difflib import get_close_matches
import re
from collections import Counter
import matplotlib.pyplot as plt
from geopy.distance import geodesic
import folium
from folium.plugins import HeatMap

sys.path.append('../Funciones')

from funciones import  obtener_establecimientos_localidad

In [2]:
comercios = ['Farmacia','Farmacias', 'Drugs Store','Hospital']

# Coordenadas Mazatlán
coordenadas = (23.247280378872777, -106.41030849227556)  
# Radio de busqueda en Kilometros 
r = 14

# Llamamos la funcion para obtener la base de comercios en la zona
base_datos= obtener_establecimientos_localidad(coordenadas, comercios,r)
base_datos.drop('ID', axis=1, inplace=True)


In [7]:
df_farmacias = base_datos[(base_datos['Establecimiento'] == 'Farmacia')|(base_datos['Establecimiento'] == 'Farmacias')|(base_datos['Establecimiento'] == 'Drugs Store')].copy()
df_farmacias.to_csv('Farmacias_Mazatlan.csv', index=False, encoding='utf-8-sig')

In [41]:
df_farmacias_denue = pd.read_csv('INEGI_DENUE_24062025.csv', encoding='ISO-8859-1')
df_farmacias_denue= df_farmacias_denue[['Nombre de la Unidad Económica','Nombre de clase de la actividad','Nombre de la vialidad','Número exterior o kilómetro','Número interior','Latitud', 'Longitud','Fecha de incorporación al DENUE']].copy()
df_farmacias_denue = df_farmacias_denue[(df_farmacias_denue['Nombre de clase de la actividad']=='Farmacias sin minisúper') |(df_farmacias_denue['Nombre de clase de la actividad']=='Farmacias con minisúper')].copy()
df_farmacias_denue.to_csv('Farmacias_DENUE_Mazatlan.csv', index=False, encoding='utf-8-sig')
df_farmacias_denue



Nombre de la Unidad Económica Nombre de clase de la actividad  \
2       BODEGA DE FARMACIA GUADALAJARA         Farmacias sin minisúper   
3        BODY FIT MAZATLAN SUPLEMENTOS         Farmacias sin minisúper   
4                        BOTICA ALCALA         Farmacias sin minisúper   
5    BRIGADA DE DISPENSARIOS POPULARES         Farmacias sin minisúper   
6             CASA NATURISTA EL TREBOL         Farmacias sin minisúper   
..                                 ...                             ...   
337                SKIN CARE SOLUTIONS         Farmacias sin minisúper   
338                     SOLO GENERICOS         Farmacias con minisúper   
339           SUPER FARMACIA ACONTECER         Farmacias con minisúper   
340            TIENDA NATURISTA AZTECA         Farmacias sin minisúper   
341                  VI SALUD FARMACIA         Farmacias sin minisúper   

    Nombre de la vialidad  Número exterior o kilómetro  Número interior  \
2         SIERRA QUEBRADA                          0.0              NaN   
3             SANTA JULIA                        113.0              NaN   
4          AQUILES SERDAN                       1710.0              0.0   
5    INTERNACIONAL AL SUR                          0.0              NaN   
6      FRANCISCO I MADERO                      11635.0              NaN   
..                    ...                          ...              ...   
337  AVENIDA DE LA MARINA                       6052.0              NaN   
338            LA PRADERA                      18114.0              0.0   
339        SERGIO GALINDO                         32.0              0.0   
340         LEANDRO VALLE                        409.0              NaN   
341    AVENIDA DEL DELFIN                          0.0              NaN   

       Latitud    Longitud Fecha de incorporación al DENUE  
2    23.242269 -106.443372                         2024-11  
3    23.254649 -106.403159                         2024-11  
4    23.202173 -106.420574                         2010-07  
5    23.217511 -106.374439                         2024-11  
6    23.279038 -106.401000                         2019-11  
..         ...         ...                             ...  
337  23.273450 -106.446797                         2024-11  
338  23.268080 -106.374117                         2014-12  
339  23.261041 -106.433154                         2010-07  
340  23.201951 -106.420461                         2019-11  
341  23.254248 -106.421173                         2024-11  

[327 rows x 8 columns]

In [60]:
df_farmacias_top = df_farmacias_denue['Nombre de la Unidad Económica'].value_counts().reset_index()
df_farmacias_top.columns = ['Nombre de la Unidad Económica', 'Frecuencia']
#df_farmacias_top.to_csv('Top_Farmacias_DENUE_Mazatlan.csv', index=False, encoding='utf-8-sig')
df_farmacias_top.head(20)

Nombre de la Unidad Económica  Frecuencia
0          FARMACIAS GUADALAJARA          18
1            FARMACIAS SIMILARES          15
2              LA NUEVA FARMACIA          15
3                   ECO FARMACIA           9
4                    ECOFARMACIA           9
5             FARMACIA SIMILARES           7
6               FARMACIAS UNISIN           5
7                   FARMACIA PVR           5
8                FARMACIA UNISIN           5
9            FARMACIA CRUZ VERDE           3
10               FARMACIA LA PAZ           3
11               FARMACIA ECORED           3
12            FARMACIA MEDIFARMA           2
13       FARMACIAS LAS POPULARES           2
14        FARMACIA DERMATOLOGICA           2
15                  ECOFARMACIAS           2
16                 ECO FARMACIAS           2
17               FARMACIA DORADA           2
18           FARMACIAS POPULARES           2
19                   FARMACLINIK           2

In [62]:
# Diccionario: nombre sucio → nombre limpio
mapa_farmacias = {
    # ECO FARMACIA
    'ECOFARMACIA': 'ECO FARMACIA',
    'ECOFARMACIAS': 'ECO FARMACIA',
    'ECO FARMACIAS': 'ECO FARMACIA',
    'ECO FARMACIA SUCURSAL IMSS': 'ECO FARMACIA',
    'ECORED FARMACIAS': 'ECO FARMACIA',
    'FARMACIA ECORED': 'ECO FARMACIA',

    # BENAVIDES
    'FARMACIAS BENAVIDES SUC M536 EJERCITO MEXICANO SIN': 'FARMACIAS BENAVIDES',
    'FARMACIAS BENAVIDES SUC N184 MAZATLAN SIN': 'FARMACIAS BENAVIDES',
    'FARMACIAS BENAVIDES SUC N723 CAMARON SABALO SIN': 'FARMACIAS BENAVIDES',
    'FARMACIAS BENAVIDES SUC N725 MONUMENTO AL PESCADOR SIN': 'FARMACIAS BENAVIDES',
    'FARMACIAS BENAVIDES SUC N756 PLAZA MONTECARLO SIN': 'FARMACIAS BENAVIDES',
    'FARMACIAS BENAVIDES SUC N761 HACIENDA DEL SEMINARIO SIN': 'FARMACIAS BENAVIDES',
    'FARMACIAS DE GENERICOS LAS POPULARES': 'FARMACIAS BENAVIDES',

    # SIMILARES
    'FARMACIA SIMILARES': 'FARMACIAS SIMILARES',
    'FARMACIAS DE SIMILARES MAZATLAN 8': 'FARMACIAS SIMILARES',
    'FARMACIAS DE SIMILARES MAZATLAN 4': 'FARMACIAS SIMILARES',
    'FARMACIAS DE SIMILARES MAZATLAN 3': 'FARMACIAS SIMILARES',
    'FARMACIAS DE SIMILARES MAZATLAN 2': 'FARMACIAS SIMILARES',
    'FARMACIAS DE SIMILARES MAZATLAN 1': 'FARMACIAS SIMILARES',
    'FARMACIAS DE SIMILARES MAZATLAN 10': 'FARMACIAS SIMILARES',
    'FARMACIAS DE SIMILARES MAZATLAN 12': 'FARMACIAS SIMILARES',
    'FARMACIAS SIMILARES F2481': 'FARMACIAS SIMILARES',
    'FARMACIAS SIMILARES F0803': 'FARMACIAS SIMILARES',
    'FARMACIAS SIMILARES F5239': 'FARMACIAS SIMILARES',
    'FARMACIAS SIMILARES FC0600': 'FARMACIAS SIMILARES',
    'FARMACIAS SIMILARES FC2298': 'FARMACIAS SIMILARES',
    'FARMACIA SIMILAR': 'FARMACIAS SIMILARES',
    'FARMACIA SIMILIARES': 'FARMACIAS SIMILARES',
    'FARMACOS ECONIMICOS': 'FARMACIAS SIMILARES',
    'FRAMACIAS SIMILARES': 'FARMACIAS SIMILARES',
    'FARMACIA SIMILARES FH0105': 'FARMACIAS SIMILARES',
    'FARMACIAS DE SIMILARES': 'FARMACIAS SIMILARES',
    'FARMACIAS DE SIMILARES NAVOLATO 3': 'FARMACIAS SIMILARES',


    # GUADALAJARA
    'BODEGA DE FARMACIA GUADALAJARA': 'FARMACIAS GUADALAJARA',

    # AHORRO
    'FARMACIAS DEL AHORRO SIN MABH BAHIA': 'FARMACIAS DEL AHORRO',
    'FARMACIAS DEL AHORRO SIN MASB SABALO': 'FARMACIAS DEL AHORRO',
    'FARMACIAS DEL AHORRO SIN MAOP OSCAR PEREZ': 'FARMACIAS DEL AHORRO',
    'FARMACIAS DEL AHORRO SIN MAME MEDITERRANEO': 'FARMACIAS DEL AHORRO',
    'FARMACIAS DEL AHORRO SIN MACS CANSECO': 'FARMACIAS DEL AHORRO',
    'FARMACIAS DEL AHORRO SIN MAJR JARIPILLO II': 'FARMACIAS DEL AHORRO',

    # Farmacias Uinisin
    'FARMACIA UNISIN': 'FARMACIA UNISIN',
	'FARMACIAS UNISIN': 'FARMACIA UNISIN',


    'DERMATOLOGICA SUAVEPIEL': 'DERMATOLOGICA SUAVEPIEL',
    'DERMATOLOGICA SUAVEPIEL 2': 'DERMATOLOGICA SUAVEPIEL',

    'FARMACIA CORAL': 'FARMACIA CORAL',
    'FARMACIA CORAL IV': 'FARMACIA CORAL',

    'FARMACIA MASALUD': 'FARMACIA MASALUD',
    'FARMACIA MAX SALUD': 'FARMACIA MASALUD',

    'LA NUEVA FARMACIA': 'LA NUEVA FARMACIA',
    'LA NUEVA FARMACIA CLINICA BICENTENARIO': 'LA NUEVA FARMACIA',
    'LA NUEVA FARMACIA ZONA DORADA': 'LA NUEVA FARMACIA',
    'LA NUEVA FARMACIQA': 'LA NUEVA FARMACIA',


    'SERVIFARMACIA URBI VILLA': 'SERVIFARMACIA',
    'SERVIFARMACIA VALLES DEL EJIDO': 'SERVIFARMACIA',
    'SERVIFARMACIA VILLA VERDE': 'SERVIFARMACIA',
    'SERVIFARMACIA VILLAS DEL REY': 'SERVIFARMACIA',
    'SERVIFARMACIAS ADMINISTRACION': 'SERVIFARMACIA'

    # YZA
    # todas las que empiezan con FARMACIAS YZA → 'FARMACIAS YZA'
}

# Limpia y reemplaza
df_farmacias_top['Cadena Farmacia'] = df_farmacias_top['Nombre de la Unidad Económica'].replace(mapa_farmacias)

# Estándar para YZA
df_farmacias_top['Cadena Farmacia'] = df_farmacias_top['Cadena Farmacia'].str.replace(r'^FARMACIAS YZA.*', 'FARMACIAS YZA', regex=True)

# Normaliza espacios y mayúsculas
df_farmacias_top['Cadena Farmacia'] = df_farmacias_top['Cadena Farmacia'].str.upper().str.strip()


df_farmacias_cadenas = df_farmacias_top.groupby('Cadena Farmacia', as_index=False)['Frecuencia'].sum()
df_farmacias_cadenas = df_farmacias_cadenas.sort_values(by='Frecuencia', ascending=False)
#df_farmacias_cadenas.to_csv('Top_Cadenas_Farmacias_DENUE_Mazatlan.csv', index=False, encoding='utf-8-sig')
df_farmacias_cadenas.head(20)

Cadena Farmacia  Frecuencia
90             FARMACIAS YZA          77
88       FARMACIAS SIMILARES          41
6               ECO FARMACIA          27
82     FARMACIAS GUADALAJARA          19
95         LA NUEVA FARMACIA          18
73           FARMACIA UNISIN          10
77       FARMACIAS BENAVIDES           7
78      FARMACIAS DEL AHORRO           6
58              FARMACIA PVR           5
103            SERVIFARMACIA           5
42           FARMACIA LA PAZ           3
20       FARMACIA CRUZ VERDE           3
5    DERMATOLOGICA SUAVEPIEL           2
19            FARMACIA CORAL           2
30           FARMACIA DORADA           2
86   FARMACIAS LAS POPULARES           2
91               FARMACLINIK           2
51        FARMACIA MEDIFARMA           2
49          FARMACIA MASALUD           2
87       FARMACIAS POPULARES           2

In [26]:

df_farmacias = base_datos[(base_datos['Establecimiento'] == 'Farmacia')|(base_datos['Establecimiento'] == 'Farmacias')|(base_datos['Establecimiento'] == 'Drugs Store')].copy()
# Crear mapa centrado
mapa = folium.Map(location=[df_farmacias['latitud'].mean(), df_farmacias['longitud'].mean()], zoom_start=16)

# Añadir marcadores
for index, row in df_farmacias.iterrows():
    folium.Marker(
        [row['latitud'], row['longitud']],
        popup=row['Nombre de establecimiento']
    ).add_to(mapa)

# Añadir mapa de calor
heat_data = df_farmacias[['latitud', 'longitud']].dropna().values.tolist()
HeatMap(heat_data, radius=15).add_to(mapa)

# Añadir leyenda personalizada
total_farmacias = len(df_farmacias)
legend_html = f"""
<div style="position: fixed;
     bottom: 50px; left: 50px; width: 250px; height: 50px;
     background-color: white; border:2px solid grey; z-index:9999;
     font-size:14px; padding: 10px;">
     <b>Total de farmacias:</b> {total_farmacias}
</div>
"""
mapa.get_root().html.add_child(folium.Element(legend_html))
# Guardar Mapa
mapa.save("Farmacias Mazatlán.html")
mapa 

In [28]:

df_farmacias = base_datos[(base_datos['Establecimiento'] == 'Farmacia')|(base_datos['Establecimiento'] == 'Farmacias')|(base_datos['Establecimiento'] == 'Drugs Store')].copy()
# Crear mapa centrado
mapa = folium.Map(location=[df_farmacias['latitud'].mean(), df_farmacias['longitud'].mean()], zoom_start=16)

# Añadir mapa de calor
heat_data = df_farmacias[['latitud', 'longitud']].dropna().values.tolist()
HeatMap(heat_data, radius=15).add_to(mapa)

# Añadir leyenda personalizada
total_farmacias = len(df_farmacias)
legend_html = f"""
<div style="position: fixed;
     bottom: 50px; left: 50px; width: 250px; height: 50px;
     background-color: white; border:2px solid grey; z-index:9999;
     font-size:14px; padding: 10px;">
     <b>Total de farmacias:</b> {total_farmacias}
</div>
"""
mapa.get_root().html.add_child(folium.Element(legend_html))
# Guardar Mapa
mapa.save("Farmacias mapa calor Mazatlán.html")
mapa

In [31]:
df_farmacias = base_datos[(base_datos['Establecimiento'] == 'Farmacia')|(base_datos['Establecimiento'] == 'Farmacias')|(base_datos['Establecimiento'] == 'Drugs Store')].copy()
# Crear mapa centrado
mapa = folium.Map(location=[df_farmacias['latitud'].mean(), df_farmacias['longitud'].mean()], zoom_start=16)

# Añadir mapa de calor
heat_data = df_farmacias[['latitud', 'longitud']].dropna().values.tolist()
HeatMap(heat_data, radius=15).add_to(mapa)

# Guardar Mapa
mapa.save("Farmacias mapa calor Mazatlán_!.html")
mapa

In [27]:
df_hopital = base_datos[base_datos['Establecimiento'] == 'Hospital'].copy()

# Crear mapa centrado
mapa = folium.Map(location=[df_hopital['latitud'].mean(), df_hopital['longitud'].mean()], zoom_start=16)

# Añadir marcadores
for index, row in df_hopital.iterrows():
    folium.Marker(
        [row['latitud'], row['longitud']],
        popup=row['Nombre de establecimiento']
    ).add_to(mapa)

# Añadir mapa de calor
heat_data = df_hopital[['latitud', 'longitud']].dropna().values.tolist()
HeatMap(heat_data, radius=15).add_to(mapa)

# Añadir leyenda personalizada
total_hospitales = len(df_hopital)
legend_html = f"""
<div style="position: fixed;
     bottom: 50px; left: 50px; width: 250px; height: 50px;
     background-color: white; border:2px solid grey; z-index:9999;
     font-size:14px; padding: 10px;">
     <b>Total de hospitales:</b> {total_hospitales}
</div>
"""
mapa.get_root().html.add_child(folium.Element(legend_html))
# Guardar Mapa
mapa.save("Hospitales Mazatlán.html")
mapa 





In [30]:
df_hopital = base_datos[base_datos['Establecimiento'] == 'Hospital'].copy()

# Crear mapa centrado
mapa = folium.Map(location=[df_hopital['latitud'].mean(), df_hopital['longitud'].mean()], zoom_start=16)

# Añadir mapa de calor
heat_data = df_hopital[['latitud', 'longitud']].dropna().values.tolist()
HeatMap(heat_data, radius=15).add_to(mapa)

# Guardar Mapa
mapa.save("Hospitales mapa calor Mazatlán_1.html")
mapa 

